**What I did**
1. Fetch all episode links of Lex Fridman Podcast from https://steno.ai
2. For each episode, transform the transcript in html to json format (Vicuna ShareGPT format)
3. remove the first few sentences from Lex for each episode to remove the introduction and ads. 

**Problems & Concerns**
1. it's a audio-to-text dataset, it contains inaccurate detections
2. although the speakers are professionals, these are verbal conversations which contain oral languages
3. it may contain ads and personal opinions from Lex Fridman and the speakers
4. ...

Try for one podcast

In [ ]:
import requests
from bs4 import BeautifulSoup
import json

url = 'https://steno.ai/lex-fridman-podcast-10/378-anna-frebel-origin-and-evolution-of-the-universe'
response = requests.get(url)
soup = BeautifulSoup(response.text, 'html.parser')

transcript_elements = soup.find_all('div', class_=['transcript is-main', 'transcript is-split'])

conversations = []
current_speaker = None
current_text = ''
starting = True
for element in transcript_elements:
    speaker_element = element.find('li', class_='speaker')
    text_element = element.find('p', class_='transcript__text tg-paragraph')
    if speaker_element and text_element:
        speaker = 'lex' if speaker_element.get_text() == 'Speaker 1' else 'guest'
        text = text_element.get_text().strip()
        if current_speaker is None:
            # This is the first speaker
            current_speaker = speaker
            current_text = text
        elif speaker == current_speaker:
            # This is the same speaker as the last one, so combine the text
            if not starting:
                current_text += ' ' + text
            else: # for the starting part, use the last paragraph only
                current_text = text
        else:
            # This is a new speaker, so add the previous conversation to the list
            starting = False
            conversations.append({'from': current_speaker, 'value': current_text})
            current_speaker = speaker
            current_text = text

# Add the last conversation
if current_text:
    conversations.append({'from': current_speaker, 'value': current_text})
print(len(conversations))
data = {
    'id': '378-anna-frebel',
    'conversations': conversations
}

# Print JSON to console
print(json.dumps(data, indent=2))

# Save JSON to file
with open('378-anna-frebel.json', 'w') as f:
    json.dump(data, f, indent=2)


Try to get all urls

In [ ]:
import requests, tqdm

base_url = "https://steno.ai/lex-fridman-podcast-10/"

# This would be a loop over all the pages you are interested in

episode_urls = []
for i in tqdm.tqdm(range(1, 66)):
    response = requests.get("https://steno.ai/lex-fridman-podcast-10/fetch-podcast?page={}".format(i))
    data = response.json()

    for episode in data['episodes']['data']:
        episode_slug = episode['slug']
        episode_url = base_url + episode_slug
        episode_urls.append(episode_url)
print(len(episode_urls))

100%|██████████| 65/65 [03:46<00:00,  3.48s/it]

387


In [ ]:
episode_urls

In [ ]:
import requests
from bs4 import BeautifulSoup
import json

def fetch_one_episode(url):
    #url = 'https://steno.ai/lex-fridman-podcast-10/378-anna-frebel-origin-and-evolution-of-the-universe'
    slug = url.split("/")[-1]
    response = requests.get(url)
    soup = BeautifulSoup(response.text, 'html.parser')

    transcript_elements = soup.find_all('div', class_=['transcript is-main', 'transcript is-split'])

    conversations = []
    current_speaker = None
    first_speaker = None
    for element in transcript_elements:
        speaker_element = element.find('li', class_='speaker')
        text_element = element.find('p', class_='transcript__text tg-paragraph')
        if speaker_element and text_element:
            text = text_element.get_text().strip()
            if first_speaker is None:
                first_speaker = speaker_element.get_text()
            
    current_text = ''
    starting = True
    for element in transcript_elements:
        speaker_element = element.find('li', class_='speaker')
        text_element = element.find('p', class_='transcript__text tg-paragraph')
        if speaker_element and text_element:
            speaker = 'lex' if speaker_element.get_text() == first_speaker else 'guest'
            text = text_element.get_text().strip()
            if current_speaker is None:
                # This is the first speaker
                current_speaker = speaker
                current_text = text
            elif speaker == current_speaker:
                # This is the same speaker as the last one, so combine the text
                if not starting:
                    current_text += ' ' + text
                else: # for the starting part, use the last paragraph only
                    current_text = text
            else:
                # This is a new speaker, so add the previous conversation to the list
                starting = False
                conversations.append({'from': current_speaker, 'value': current_text})
                current_speaker = speaker
                current_text = text

    # Add the last conversation
    if current_text:
        conversations.append({'from': current_speaker, 'value': current_text})
    #print(len(conversations))
    data = {
        'id': slug,
        'conversations': conversations
    }
    return data


In [ ]:
all_data = []
for episode_url in tqdm.tqdm(episode_urls):
    episode_data = fetch_one_episode(episode_url)
    all_data.append(episode_data)

100%|██████████| 387/387 [25:06<00:00,  3.89s/it]


In [ ]:
with open('lex_fridman_podcast_for_llm_vicuna_original.json', 'w') as f:
    json.dump(all_data, f, indent=2)

In [98]:
all_data = json.loads(open("lex_fridman_podcast_for_llm_vicuna_original.json").read())

In [99]:
def chunk_conversation(conversation, limit=1200):
    chunked_conversations = []
    chunk = []
    word_count = 0
    chunk_id = 0
    count = 0

    for entry in conversation["conversations"]:
        entry_word_count = len(entry['value'].split())
        if word_count + entry_word_count > limit and count % 2 == 0: # count % 2 == 0: making sure each conversation starts with lex
            chunked_conversations.append({
                "id": f"{conversation['id']}-{chunk_id}",
                "conversations": chunk
            })
            chunk = []
            word_count = 0
            chunk_id += 1
        chunk.append(entry)
        word_count += entry_word_count
        count += 1

    if chunk:  # add the last chunk if any left
        chunked_conversations.append({
            "id": f"{conversation['id']}-{chunk_id}",
            "conversations": chunk
        })

    return chunked_conversations


In [100]:
all_data_chunked = []
for each in all_data:
    each_data_chunked = chunk_conversation(each)
    all_data_chunked += each_data_chunked

In [101]:
with open('lex_fridman_podcast_for_llm_vicuna_chunked.json', 'w') as f:
    json.dump(all_data_chunked, f, indent=2)

change "lex" & "guest" to "human" & "gpt" for vicuna training

In [102]:
for conv in all_data_chunked:
    for each in conv["conversations"]:
        each["from"] = "human" if each["from"] == "lex" else "gpt"

In [103]:
with open('lex_fridman_podcast_for_llm_vicuna_chunked_gpt.json', 'w') as f:
    json.dump(all_data_chunked, f, indent=2)

Save to huggingface

In [ ]:
!pip install huggingface_hub

In [ ]:
from huggingface_hub import notebook_login, HfApi
notebook_login()

In [ ]:
api = HfApi()
api.upload_file(
    path_or_fileobj="/content/lex_fridman_podcast_for_llm_vicuna_chunked.json",
    path_in_repo="/other_versions/lex_fridman_podcast_for_llm_vicuna_chunked.json",
    repo_id="64bits/lex_fridman_podcast_for_llm_vicuna",
    repo_type="dataset",
)

Use Dataset

In [68]:
!pip install -q datasets

In [111]:
from datasets import load_dataset

dataset = load_dataset("64bits/lex_fridman_podcast_for_llm_vicuna")

Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

  0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
dataset["train"][0]